Done: P(H|H first vis) and P(H|L first vis) social 

To-do:
- P(H|H first vis) and P(H|L first vis) solos
- Subtract solo-social sensory effects
- Output sensory effects across wall separations

Functions and imports


In [2]:
import sys
import os

parent_dir = os.path.abspath(os.path.join(os.getcwd(), "..", "..", ".."))
main_copy_dir = os.path.join(parent_dir, "main_copy")
octagon_analysis = os.path.join(parent_dir, "octagon_analysis")
sys.path.append(main_copy_dir)
sys.path.append(octagon_analysis)

print("Added paths to sys.path:", main_copy_dir, octagon_analysis)

Added paths to sys.path: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy /Users/benny/Desktop/MSc/Project/Git/repos/octagon_analysis


Imports with autoreload

In [3]:
%load_ext autoreload
%autoreload 2

import analysis.trajectory_efficiency as trajectory_efficiency
import pandas as pd
import numpy as np
import parse_data.prepare_data as prepare_data
import parse_data.identify_filepaths as identify_filepaths
import analysis.conditioned_player_choice as conditioned_player_choice
import prepare_questionnaire_data
import data_extraction.get_indices as get_indices
import globals

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


Define data folder and eprsonal data file

In [4]:
data_folder = '/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files'
personal_data_csv = '/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/questionnaire_data/personal_data.csv'

Prepare questionnaire data

In [5]:
questionnaire_data_df = prepare_questionnaire_data.preprocess_data()

AQ_scores.csv
GAD_scores.csv
BIS_scores.csv


/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/questionnaire_data/prepare_questionnaire_data.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = df[column_name].replace(answers_dict[trait]).astype(int)
/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/questionnaire_data/prepare_questionnaire_data.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = df[column_name].replace(answers_dict[trait]).astype(int)
/Users/benny

Get social and solo filenames (solos ordered by pseudonym, neither ordered by date)

In [6]:
social_files, ordered_solos = identify_filepaths.get_filenames(data_folder=data_folder)

In [7]:
len(ordered_solos)

198

Separate first and second solos into lists

In [7]:
first_solos = ordered_solos[::2]
second_solos = ordered_solos[1::2]

Create list of tuples for pseudonyms in socials

In [8]:
import re
pseudo_tuples_list = []
experiment_dates_socials = []
for file in social_files:
     # match the session number and the pseudonym string
    match = re.search(r'(\d+_\d)[/\\](\d{4}-\d{2}-\d{2})_(\d{2}-\d{2}-\d{2})_(.*?_.*?)_Social\.json', file)
    if match:
        session, date, time, pseudonyms = match.groups()
        pseudo_tuples = pseudonyms.split('_')[0::]
        pseudo_tuples_list.append(pseudo_tuples)
        experiment_dates_socials.append(date)

In [9]:
social_dates = {}
opponent_dict = {}

for i, pseudonym in enumerate(pseudo_tuples_list):
    player0 = pseudonym[0]
    player1 = pseudonym[1]

    if player0 not in social_dates:
        social_dates[player0] = []
        opponent_dict[player0] = []
    if player1 not in social_dates:
        social_dates[player1] = []
        opponent_dict[player1] = []

    social_dates[player0] = experiment_dates_socials[i]
    social_dates[player1] = experiment_dates_socials[i]

    opponent_dict[player0] = player1
    opponent_dict[player1] = player0


Create list of pseudonyms for first and second solos (in case they are differently ordered, or some are missing I guess?)

In [10]:
first_solo_pseudo_list = []
second_solo_pseudo_list = []
first_solo_dates = []
second_solo_dates = []
solo_dates = {}


for first_solo, second_solo in zip(first_solos, second_solos):
   # match the session number and the pseudonym string
    first_match = re.search(r'(\d+_\d)[/\\](\d{4}-\d{2}-\d{2})_(\d{2}-\d{2}-\d{2})_(.*?)_FirstSolo\.json', first_solo)
    second_match = re.search(r'(\d+_\d)[/\\](\d{4}-\d{2}-\d{2})_(\d{2}-\d{2}-\d{2})_(.*?)_SecondSolo\.json', second_solo)

    if first_match:
        session, date, time, pseudonyms = first_match.groups()
        first_pseudo = pseudonyms.split('_')[0::]
        first_solo_pseudo_list.append(first_pseudo)
        first_solo_dates.append(date)

        
    if second_match:
        session, date, time, pseudonyms = second_match.groups()
        second_pseudo = pseudonyms.split('_')[0::]
        second_solo_pseudo_list.append(second_pseudo)
        second_solo_dates.append(date)

for i, pseudonym in enumerate(first_solo_pseudo_list):
    player = pseudonym[0]
    if player not in solo_dates:
        solo_dates[player] = []
    solo_dates[player] = first_solo_dates[i]

Prepare data and get trial lists

In [11]:
df_solos, solos_lists = prepare_data.prepare_data(data_folder, ordered_solos, combine=False)
df_socials, social_lists = prepare_data.prepare_data(data_folder, social_files, combine=False)

filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-09-51_CY17_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-46-27_CY17_SecondSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-10-56_RL17_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-46-05_RL17_SecondSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/241112_2/2024-11-12_15-13-34_FA12_FirstSolo.json
Loading complete.
Preprocessin

In [12]:
df_first_solos, first_solos_lists = prepare_data.prepare_data(data_folder, first_solos, combine=False)
df_second_solos, second_solos_lists = prepare_data.prepare_data(data_folder, second_solos, combine=False)

filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-09-51_CY17_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/250417_1/2025-04-17_12-10-56_RL17_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/241112_2/2024-11-12_15-13-34_FA12_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/241112_2/2024-11-12_15-11-45_SL12_FirstSolo.json
Loading complete.
Preprocessing complete.
filepath: /Users/benny/Desktop/MSc/Project/Git/repos/main_copy/questionnaire_analysis/pseudonymised_json_files/241210_1/2024-12-10_14-13-47_TE10_FirstSolo.json
Loading complete.
Preprocessing 

Combine solos and trial lists

In [13]:
# combined solos
combined_solos = []

for trial_list_idx in range(0, len(solos_lists), 2):

    print(ordered_solos[trial_list_idx], ordered_solos[trial_list_idx + 1]) 

    # concatenate the trial lists for the 2 solos of this session
    trial_list_combined = solos_lists[trial_list_idx] + solos_lists[trial_list_idx + 1]

    combined_solos.append(trial_list_combined)

250417_1/2025-04-17_12-09-51_CY17_FirstSolo.json 250417_1/2025-04-17_12-46-27_CY17_SecondSolo.json
250417_1/2025-04-17_12-10-56_RL17_FirstSolo.json 250417_1/2025-04-17_12-46-05_RL17_SecondSolo.json
241112_2/2024-11-12_15-13-34_FA12_FirstSolo.json 241112_2/2024-11-12_15-44-54_FA12_SecondSolo.json
241112_2/2024-11-12_15-11-45_SL12_FirstSolo.json 241112_2/2024-11-12_15-45-35_SL12_SecondSolo.json
241210_1/2024-12-10_14-13-47_TE10_FirstSolo.json 241210_1/2024-12-10_14-45-41_TE10_SecondSolo.json
241210_1/2024-12-10_14-12-58_TK10_FirstSolo.json 241210_1/2024-12-10_14-45-09_TK10_SecondSolo.json
250509_1/2025-05-09_12-18-03_AM09_FirstSolo.json 250509_1/2025-05-09_12-53-10_AM09_SecondSolo.json
250509_1/2025-05-09_12-18-53_MC09_FirstSolo.json 250509_1/2025-05-09_12-53-00_MC09_SecondSolo.json
250401_2/2025-04-01_15-17-03_AL01_FirstSolo.json 250401_2/2025-04-01_15-52-21_AL01_SecondSolo.json
250401_2/2025-04-01_15-17-26_NL01_FirstSolo.json 250401_2/2025-04-01_15-52-54_NL01_SecondSolo.json
250319_1/2

Create pseudonym list for combined solos - will be the same as first/second solos without the extra first solo that doesn't have a second solo match
- Now that the latter is removed the pseudonym lists should really all be the same, just need to check

In [14]:
combined_solo_pseudo_list = second_solo_pseudo_list
combined_solo_dates = second_solo_dates

In [112]:
for i in range(len(combined_solo_pseudo_list)):
    if combined_solo_pseudo_list[i] != first_solo_pseudo_list[i]:
        print('no')

Choice conditioned on visibility, using conditioned_player_choice.py

Solo-social difference needs matching by pseudonym first

P(H|H first vis)
- first solo X
- second solo X
- combined solo X
- social x
- combined solo - social
- wall sep 1 X
- wall sep 2 X
- wall sep 4 X

P(H|L first vis)
- first solo
- second solo
- combined solo
- social
- combined solo - social
- wall sep 1
- wall sep 2
- wall sep 4

P(H|opponent vis)
- first solo
- second solo
- combined solo
- social
- combined solo - social
- wall sep 1
- wall sep 2
- wall sep 4

P(H|opponent not vis)
- first solo
- second solo
- combined solo
- social
- combined solo - social
- wall sep 1
- wall sep 2
- wall sep 4

P(win)
- first solo
- second solo
- combined solo
- social
- combined solo - social
- wall sep 1
- wall sep 2
- wall sep 4

Score per unit time
- first solo
- second solo
- combined solo
- social
- combined solo - social
- wall sep 1
- wall sep 2
- wall sep 4

- match to pseudonym and store in table


SOLO P(H|H first vis)

filtered to include HighLow trials only

1. First solos
2. Second solos
3. Combined solos

In [15]:

# variables
inferred_choice = False
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = None
solo = True
data_size_cutoff = 6

In [16]:
## First solo datasets
(probabilities1firstsolo,
 numerator1firstsolo,
  denominator1firstsolo) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(first_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 1. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0.
 0. 1. 0. 0. 1. 0. 0.]
And the number of valid trials at this step is 14
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 0. 0. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0.]
And the number of valid trials at this step is 11
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 1. 1. 1. 1. 1. 0. 0.
 0. 0.]
And the number of valid trials at this step is 9
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
 0. 0.]
And the number of 

In [17]:
## Second solo datasets
(probabilities1secondsolo,
 numerator1secondsolo,
  denominator1secondsolo) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(second_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 1. 0. 1.]
And the number of valid trials at this step is 11
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 0. 0. 1. 1. 1. 0. 1. 0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 1. 1. 1.
 1. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 1. 0. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0.]
And the number of valid trials at this step is 20
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 1. 1. 1. 0. 0. 1. 1. 0. 0. 1. 0. 1. 0.
 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 1. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0.
 1. 1. 0. 0. 0. 0. 1.]
And the number of valid trials at this step is 22
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1

In [18]:
## Combined solo datasets
(probabilities1combinedsolo,
 numerator1combinedsolo,
  denominator1combinedsolo) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(combined_solos, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 1. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0.
 0. 1. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0.
 1. 0. 1.]
And the number of valid trials at this step is 25
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 0. 0. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 1.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 1. 0. 1. 0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 1.
 1. 1. 1. 0. 0. 1. 1. 0. 0. 0. 1. 0. 0. 1. 0. 1. 1. 1. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
And the number of valid trials at this step is 31
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 0. 1. 0. 0. 0.

In [26]:
len(numerator1combinedsolo[1]), len(denominator1combinedsolo[1])

(29, 31)

Filter by wall separations

Wall sep: 45°

In [19]:

# variables
inferred_choice = False
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 1
solo = True
data_size_cutoff = 6

In [188]:
## First solo datasets
(probabilities1firstsolo_sep1,
 numerator1firstsolo_sep1,
  denominator1firstsolo_sep1) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(first_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
 0. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
And the number of valid trials at this step is 6
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.
 0. 0. 0. 0.]
And the number of valid trials at this step is 6
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 1. 0. 0.]
And the number of valid trials at this step is 2
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 0. 1. 0. 0. 0. 1. 0. 0. 1.]
And th

In [189]:
## Second solo datasets
(probabilities1secondsolo_sep1,
 numerator1secondsolo_sep1,
  denominator1secondsolo_sep1) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(second_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 1. 1. 0.
 1.]
And the number of valid trials at this step is 7
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 0. 0.]
And the number of valid trials at this step is 7
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 1. 0. 1. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 1. 0. 0. 0. 0. 1.]
And the number of valid trials at this step is 9
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0.
 0. 0.]
And the number of valid trials at this step is 4
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wal

In [20]:
## Combined solo datasets
(probabilities1combinedsolo_sep1,
 numerator1combinedsolo_sep1,
  denominator1combinedsolo_sep1) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(combined_solos, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0.
 0. 1. 0. 0. 0. 1. 0. 1. 1. 0. 1.]
And the number of valid trials at this step is 13
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0.
 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 0. 0.]
And the number of valid trials at this step is 13
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 1. 1. 1. 1. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1.]
And the number of valid trials at this step is 11
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 0. 1. 0. 0. 0. 1. 0. 0. 1. 0. 0. 0. 0.

Wall sep: 90°

In [21]:

# variables
inferred_choice = False
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 2
solo = True
data_size_cutoff = 6

In [192]:
## First solo datasets
(probabilities1firstsolo_sep2,
 numerator1firstsolo_sep2,
  denominator1firstsolo_sep2) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(first_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 1.]
And the number of valid trials at this step is 5
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 0.]
And the number of valid trials at this step is 4
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 0.]
And the number of valid trials at this step is 5
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 0.]
And the number of valid trials at this step is 0
fewer than 6 trials in the denominator, returning np.nan instead of probability
fi

In [193]:
## Second solo datasets
(probabilities1secondsolo_sep2,
 numerator1secondsolo_sep2,
  denominator1secondsolo_sep2) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(second_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 0. 0. 0. 1. 0.]
And the number of valid trials at this step is 1
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 0. 1. 0. 1. 0. 1. 1. 0. 1. 0. 0. 0. 0. 0. 0.]
And the number of valid trials at this step is 6
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 1. 0. 0. 1. 0.]
And the number of valid trials at this step is 4
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 1. 0. 1. 1. 1. 1. 1. 1. 1. 1. 0.]
And the number of valid trials at this step is 10
filter_trials_one_wall_becomes_visible_first - given_wall_first_visib

In [22]:
## Combined solo datasets
(probabilities1combinedsolo_sep2,
 numerator1combinedsolo_sep2,
  denominator1combinedsolo_sep2) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(combined_solos, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
And the number of valid trials at this step is 6
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 0. 1. 0. 0.
 0. 0. 0. 0.]
And the number of valid trials at this step is 10
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 0. 1. 1. 1. 0. 0. 1. 0.]
And the number of valid trials at this step is 9
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 1. 1. 1. 1. 1. 1. 0.]
And the number of valid trials at this step is 10
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 1. 1. 0

Wall sep: 180°

In [23]:

# variables
inferred_choice = False
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 4
solo = True
data_size_cutoff = 6

In [196]:
## First solo datasets
(probabilities1firstsolo_sep4,
 numerator1firstsolo_sep4,
  denominator1firstsolo_sep4) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(first_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 1. 0. 0. 1.]
And the number of valid trials at this step is 3
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
And the number of valid trials at this step is 1
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 1.]
And the number of valid trials at this step is 2
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 0. 0. 0. 0. 0. 0.]
And the number of valid trials at this step is 1
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_v

In [197]:
## Second solo datasets
(probabilities1secondsolo_sep4,
 numerator1secondsolo_sep4,
  denominator1secondsolo_sep4) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(second_solos_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 1. 0. 0. 1. 0.]
And the number of valid trials at this step is 3
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 1. 1. 1. 1. 0. 0. 0. 1. 0. 0. 0.]
And the number of valid trials at this step is 7
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 1. 0. 0. 1. 0. 0. 1. 1. 1. 1. 1. 1.]
And the number of valid trials at this step is 9
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 0. 1. 0. 1. 0. 1. 1. 1. 0. 1. 1. 1. 0.]
And the number of valid trials at this step is 9
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 1. 1. 0.]
And the number of valid trials at this step is 4
fewer than 6 trials in the denominator, returning np.

In [24]:
## Combined solo datasets
(probabilities1combinedsolo_sep4,
 numerator1combinedsolo_sep4,
  denominator1combinedsolo_sep4) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(combined_solos, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)
    

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 1. 0.]
And the number of valid trials at this step is 6
fewer than 6 trials in the denominator, returning np.nan instead of probability
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 1. 1. 1. 1. 0. 0. 0. 1. 0. 0. 0.]
And the number of valid trials at this step is 8
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 1. 1. 0. 0. 0. 1. 0. 0. 1. 0. 0. 1. 1. 1. 1. 1. 1.]
And the number of valid trials at this step is 11
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 1. 0. 1. 1. 1. 0. 1. 1. 1. 0.]
And the number of valid trials at this step is 10
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 1. 1. 1. 1.

SOCIALS

In [25]:

# variables
inferred_choice = True
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = None
solo = False
data_size_cutoff = 6

In [26]:
## All social datasets
(probabilities1social,
 numerator1social,
  denominator1social) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(social_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)

/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/trajectory_analysis/trajectory_vectors.py:324: RuntimeWarning: invalid value encountered in scalar divide
  cosine_similarity_this_wall = dot_product[wall_num]/(player_to_alcove_vector_norms[wall_num] * player_vector_norm)


filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 1. 1. 1. 0. 0. 1. 1. 1. 0. 1. 1. 0. 1. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 0. 0. 1. 1. 1. 0. 1. 1. 0. 1. 1. 1. 1.
 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 1. 1. 0. 0. 0. 0. 1. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 1. 0. 1. 1. 1. 1. 1. 0. 1. 0. 0. 0. 1. 1. 1. 0.
 0. 0. 1. 0. 0. 0. 1. 0. 1. 1. 0. 1. 1. 0. 1. 0. 1. 0.]
And the number of valid trials at this step is 53
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 1. 1. 0. 0. 0. 0. 1. 1. 0. 1. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0. 1. 1.
 1. 0. 1. 0. 1. 0. 1. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 1.
 1. 0. 1. 1. 0. 0. 0. 1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 1. 1.
 0. 0. 1. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1. 1. 0. 1. 1. 0. 1. 0. 1. 1. 1. 1.
 0. 0. 1. 0. 1. 0. 1. 1. 0. 0. 1. 1. 0. 0.]
And the number of valid trials at this step is 48


/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/analysis/loser_inferred_choice.py:47: RuntimeWarning: Mean of empty slice
  return np.argmax(np.nanmean(cosine_similarity_trajectory, axis=1))
/Users/benny/Desktop/MSc/Project/Git/repos/main_copy/analysis/loser_inferred_choice.py:149: RuntimeWarning: Mean of empty slice
  highest_alignment_val = np.max(np.nanmean(cosine_similarity_trajectory, axis=1))


filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 1. 0. 1. 0. 1. 1. 1. 0. 0. 0. 0. 1. 0. 1. 0. 1. 1. 1. 0. 1.
 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 1. 1. 1. 0. 0.
 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 1. 1. 1. 0. 0.
 1. 0. 1. 0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0.]
And the number of valid trials at this step is 37
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 1.
 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0.
 0. 1. 0. 1. 0. 1. 0. 1. 1. 1. 0. 0. 1. 0. 1. 0. 0. 1. 1. 1. 0. 0. 1. 1.
 0. 0. 1.]
And the number of valid trials at this step is 25
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 0. 1. 1. 0. 1. 0. 0. 1. 0. 0. 1. 0. 1. 0.
 1. 0. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 

Filter by wall sep

Wall sep: 45°

In [27]:
# variables
inferred_choice = True
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 1
solo = False
data_size_cutoff = 6

In [28]:
## All social datasets
(probabilities1social_sep1,
 numerator1social_sep1,
  denominator1social_sep1) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(social_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 0. 1. 1. 1. 0. 0. 0. 0. 1. 0. 1. 1. 0.
 1. 1. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 1. 1. 0. 0. 1. 0. 0. 1. 0. 0. 1. 1.
 1. 1. 0. 1. 0. 0. 0. 1. 0. 1. 0. 0. 1.]
And the number of valid trials at this step is 27
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 0. 0. 1. 0. 1. 0. 0. 0. 0. 0. 1. 1. 1. 1. 0. 1. 0. 0. 0. 0. 0.
 0. 0. 1. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 1. 1. 0. 1. 0. 0. 0. 1. 0. 0. 1.
 1. 0. 1. 1. 1. 1. 1. 0. 0. 1. 0.]
And the number of valid trials at this step is 24
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 1. 1. 1. 0. 0. 0. 1. 0. 1. 1. 0. 1. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0.
 0. 0. 0. 1. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 1. 0. 1. 1. 0. 0. 0. 0. 0.]
And the number of valid trials at this step is 18
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_sessi

Wall sep: 90°

In [29]:
# variables
inferred_choice = True
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 2
solo = False
data_size_cutoff = 6

In [30]:
## All social datasets
(probabilities1social_sep2,
 numerator1social_sep2,
  denominator1social_sep2) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(social_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 0. 1. 1. 1. 1. 1. 0. 0. 1. 0. 1. 0. 0. 1. 0. 1. 0. 1. 0. 0. 1.
 1. 1. 0.]
And the number of valid trials at this step is 14
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 0. 1. 0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 0. 0. 1. 0. 0. 1. 0. 0. 1.
 1. 1.]
And the number of valid trials at this step is 11
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 1. 1. 0. 0. 1. 1. 0. 0. 1. 0. 0.]
And the number of valid trials at this step is 7
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 1. 0. 1. 1. 0. 1.]
And the number of valid trials at this step is 7
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 0. 1. 1. 0. 0. 0. 0. 1. 1. 0. 0. 1. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0.
 0. 0. 1

Wall sep: 180°

In [31]:
# variables
inferred_choice = True
current_fov = 110
chosen_wall_index = 0
visible_wall_index = 0
wall_initial_vis_only = False
other_visible = None
inverse_other_visible = False
wall_sep = 4
solo = False
data_size_cutoff = 6

In [32]:
## All social datasets
(probabilities1social_sep4,
 numerator1social_sep4,
  denominator1social_sep4) = conditioned_player_choice.probability_trial_outcome_given_conditions_all_sessions(social_lists, inferred_choice, current_fov,
                                                            chosen_wall_index=chosen_wall_index, visible_wall_index=visible_wall_index,
                                                            other_visible=other_visible, wall_initial_vis_only=wall_initial_vis_only,
                                                            wall_sep=wall_sep, inverse_other_visible=inverse_other_visible, solo=solo,
                                                            trial_type=globals.HIGH_LOW, data_size_cutoff=data_size_cutoff, debug=False)

filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 0. 0. 0. 1. 0. 0. 1. 0. 1. 1. 0. 1. 0. 0. 1. 1. 0. 0. 0. 1.
 1. 0.]
And the number of valid trials at this step is 12
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 0. 1. 0. 1. 0. 0. 1. 1. 1. 1. 0. 0. 0. 1. 1. 0. 1. 1. 0. 0.
 0.]
And the number of valid trials at this step is 13
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 1. 0. 1. 1. 0. 0. 0. 0. 0. 1. 1. 1. 0. 0. 1. 1. 1. 0. 1. 0. 1.]
And the number of valid trials at this step is 12
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[0. 0. 1. 1. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 1. 1. 0. 1.]
And the number of valid trials at this step is 8
filter_trials_one_wall_becomes_visible_first - given_wall_first_visible_session array:
[1. 0. 0. 1. 0. 1. 0. 0. 0. 1. 0. 1. 1. 1. 1. 0. 0. 1. 1. 1. 0. 1.]
And the n

In [54]:
len(probabilities1social_sep4)

50

In [56]:
len(denominator1social_sep4[0])

50

Collecting denominator results for number of trials

In [ ]:
denominator1social_sep1
denominator1social_sep2
denominator1social_sep4
denominator1social

denominator1combinedsolo_sep1
denominator1combinedsolo_sep2
denominator1combinedsolo_sep4
denominator1combinedsolo
denominator1firstsolo
denominator1secondsolo


Pseudonym assignments + storing in dictionaries

In [35]:
#first_solo_high_first_sep_1 = {}
#second_solo_high_first_sep_1 = {}
combined_solo_high_first_sep_1 = {}
social_high_first_sep_1 = {}

#first_solo_high_first_sep_2 = {}
#second_solo_high_first_sep_2 = {}
combined_solo_high_first_sep_2 = {}
social_high_first_sep_2 = {}

#first_solo_high_first_sep_4 = {}
#second_solo_high_first_sep_4 = {}
combined_solo_high_first_sep_4 = {}
social_high_first_sep_4 = {}

first_solo_high_first = {}
second_solo_high_first = {}
combined_solo_high_first = {}
social_high_first = {}

social_high_first_sep_1_den = {}
social_high_first_sep_2_den = {}
social_high_first_sep_4_den = {}
social_high_first_den = {}

combinedsolo_high_first_sep_1_den = {}
combinedsolo_high_first_sep_2_den = {}
combinedsolo_high_first_sep_4_den = {}
combinedsolo_high_first_den = {}

firstsolo_high_first_den = {}
secondsolo_high_first_den = {}

In [33]:
social_suffix_map = {
    'sep_1': {
        'probability': probabilities1social_sep1,
        'denominator': denominator1social_sep1
    },
    'sep_2': {
        'probability': probabilities1social_sep2,
        'denominator': denominator1social_sep2
    },
    'sep_4': {
        'probability': probabilities1social_sep4,
        'denominator': denominator1social_sep4
    },
    'all_seps': {
        'probability': probabilities1social,
        'denominator': denominator1social
    }
}


In [34]:
solo_suffix_map = {
    'sep_1': {
        'probability': probabilities1combinedsolo_sep1,
        'denominator': denominator1combinedsolo_sep1
    },
    'sep_2': {
        'probability': probabilities1combinedsolo_sep2,
        'denominator': denominator1combinedsolo_sep2
    },
    'sep_4': {
        'probability': probabilities1combinedsolo_sep4,
        'denominator': denominator1combinedsolo_sep4
    },
    'all_seps': {
        'probability': probabilities1combinedsolo,
        'denominator': denominator1combinedsolo
    }
}

separated_solo_suffix_map = {
    'first_solo': {
        'probability': probabilities1firstsolo,
        'denominator': denominator1firstsolo
    },
    'second_solo': {
        'probability': probabilities1secondsolo,
        'denominator': denominator1secondsolo
    }
}


In [36]:
social_dict_map = {
    'sep_1': {
        'probability': social_high_first_sep_1,
        'denominator': social_high_first_sep_1_den
    },
    'sep_2': {
        'probability': social_high_first_sep_2,
        'denominator': social_high_first_sep_2_den
    },
    'sep_4': {
        'probability': social_high_first_sep_4,
        'denominator': social_high_first_sep_4_den
    },
    'all_seps': {
        'probability': social_high_first,
        'denominator': social_high_first_den
    }
}

In [37]:
solo_dict_map = {
    'sep_1': {
        'probability': combined_solo_high_first_sep_1,
        'denominator': combinedsolo_high_first_sep_1_den
    },
    'sep_2': {
        'probability': combined_solo_high_first_sep_2,
        'denominator': combinedsolo_high_first_sep_2_den
    },
    'sep_4': {
        'probability': combined_solo_high_first_sep_4,
        'denominator': combinedsolo_high_first_sep_4_den
    },
    'all_seps': {
        'probability': combined_solo_high_first,
        'denominator': combinedsolo_high_first_den
    }
}

separated_solo_dict_map = {
    'first_solo': {
        'probability': first_solo_high_first,
        'denominator': firstsolo_high_first_den
    },
    'second_solo': {
        'probability': second_solo_high_first,
        'denominator': secondsolo_high_first_den
    }
}

In [41]:
for i, (player0, player1) in enumerate(pseudo_tuples_list):
    for player in (player0, player1):
        # Initialize if not already
        for suffix_dict in social_dict_map.values():
            print(suffix_dict)
            for kind in ['probability', 'denominator']:
                if kind not in suffix_dict:
                    suffix_dict[kind] = {}
                if player not in suffix_dict[kind]:
                    suffix_dict[kind][player] = []

    for suffix, data_arrays in social_suffix_map.items():
        social_dict_map[suffix]['probability'][player0] = data_arrays['probability'][i, 0]
        social_dict_map[suffix]['probability'][player1] = data_arrays['probability'][i, 1]
        social_dict_map[suffix]['denominator'][player0] = len(data_arrays['denominator'][0][i])
        social_dict_map[suffix]['denominator'][player1] = len(data_arrays['denominator'][1][i])

{'probability': {'CY17': np.float64(0.9259259259259259), 'RL17': np.float64(0.7916666666666666), 'FA12': np.float64(0.9444444444444444), 'SL12': np.float64(0.8), 'TE10': np.float64(0.8461538461538461), 'TK10': np.float64(0.7), 'AM09': np.float64(0.7692307692307693), 'MC09': np.float64(nan), 'AL01': np.float64(0.5), 'NL01': np.float64(0.7777777777777778), 'HL19': np.float64(0.5), 'AW19': np.float64(0.7222222222222222), 'YL15': np.float64(0.6), 'RR15': np.float64(0.631578947368421), 'SS22': np.float64(nan), 'AD22': np.float64(nan), 'NK13': np.float64(0.9090909090909091), 'RD13': np.float64(0.9230769230769231), 'AV19': np.float64(0.7272727272727273), 'XG19': np.float64(0.8333333333333334), 'SH27': np.float64(nan), 'EN27': np.float64(1.0), 'SP17': np.float64(0.7), 'AW17': np.float64(0.75), 'AR10': np.float64(1.0), 'MY10': np.float64(0.5), 'JU19': np.float64(0.9090909090909091), 'SY19': np.float64(0.7), 'NO12': np.float64(0.9), 'AS12': np.float64(0.9285714285714286), 'IN04': np.float64(1.0)

In [ ]:
for i, pseudonym in enumerate(combined_solo_pseudo_list):
    player = pseudonym[0]
    for solo_suffix_dict in solo_dict_map.values():
        print(solo_suffix_dict)
        for kind in ['probability', 'denominator']:
            if kind not in solo_suffix_dict:
                solo_suffix_dict[kind] = {}
            if player not in solo_suffix_dict[kind]:
                solo_suffix_dict[kind][player] = []

    for suffix, data_arrays in solo_suffix_map.items():
        print(suffix)
        print(data_arrays['probability'][i])
        #for kind in ['probability', 'denominator']:
        solo_dict_map[suffix]['probability'][player] = data_arrays['probability'][i]
        solo_dict_map[suffix]['denominator'][player] = len(data_arrays['denominator'][i])

{'probability': {'CY17': np.float64(0.9230769230769231), 'RL17': np.float64(0.8461538461538461), 'FA12': np.float64(0.8181818181818182), 'SL12': np.float64(1.0), 'TE10': np.float64(nan), 'TK10': np.float64(nan), 'AM09': np.float64(1.0), 'MC09': np.float64(1.0), 'AL01': np.float64(0.7272727272727273), 'NL01': np.float64(0.9166666666666666), 'HL19': np.float64(1.0), 'AW19': np.float64(1.0), 'YL15': np.float64(1.0), 'RR15': np.float64(1.0), 'SS22': np.float64(1.0), 'AD22': np.float64(nan), 'NK13': np.float64(nan), 'RD13': np.float64(0.7777777777777778), 'AV19': np.float64(1.0), 'XG19': np.float64(nan), 'SH27': np.float64(nan), 'EN27': np.float64(1.0), 'SP17': np.float64(nan), 'AW17': np.float64(1.0), 'AR10': np.float64(1.0), 'MY10': np.float64(1.0), 'JU19': np.float64(1.0), 'SY19': np.float64(nan), 'NO12': np.float64(1.0), 'AS12': np.float64(0.9285714285714286), 'IN04': np.float64(0.9090909090909091), 'ZS20': np.float64(nan), 'VC20': np.float64(0.9090909090909091), 'KC14': np.float64(nan)

In [53]:
for i, pseudonym in enumerate(first_solo_pseudo_list):
    player = pseudonym[0]
    for separated_solo_suffix_dict in separated_solo_dict_map.values():
        print(separated_solo_suffix_dict)
        for kind in ['probability', 'denominator']:
            if kind not in separated_solo_suffix_dict:
                separated_solo_suffix_dict[kind] = {}
            if player not in separated_solo_suffix_dict[kind]:
                separated_solo_suffix_dict[kind][player] = []

    for suffix, data_arrays in separated_solo_suffix_map.items():
        print(suffix)
        print(data_arrays['probability'][i])
        #for kind in ['probability', 'denominator']:
        separated_solo_dict_map[suffix]['probability'][player] = data_arrays['probability'][i]
        separated_solo_dict_map[suffix]['denominator'][player] = len(data_arrays['denominator'][i])

{'probability': {}, 'denominator': {}}
{'probability': {}, 'denominator': {}}
first_solo
0.9285714285714286
second_solo
1.0
{'probability': {'CY17': np.float64(0.9285714285714286)}, 'denominator': {'CY17': 14}}
{'probability': {'CY17': np.float64(1.0)}, 'denominator': {'CY17': 11}}
first_solo
0.8181818181818182
second_solo
1.0
{'probability': {'CY17': np.float64(0.9285714285714286), 'RL17': np.float64(0.8181818181818182)}, 'denominator': {'CY17': 14, 'RL17': 11}}
{'probability': {'CY17': np.float64(1.0), 'RL17': np.float64(1.0)}, 'denominator': {'CY17': 11, 'RL17': 20}}
first_solo
0.6666666666666666
second_solo
1.0
{'probability': {'CY17': np.float64(0.9285714285714286), 'RL17': np.float64(0.8181818181818182), 'FA12': np.float64(0.6666666666666666)}, 'denominator': {'CY17': 14, 'RL17': 11, 'FA12': 9}}
{'probability': {'CY17': np.float64(1.0), 'RL17': np.float64(1.0), 'FA12': np.float64(1.0)}, 'denominator': {'CY17': 11, 'RL17': 20, 'FA12': 22}}
first_solo
nan
second_solo
1.0
{'probabil

Example: access solo_dict_map['first_solo_high_first']['probability'][pseudonym] for pH in first solo across all wall seps

In [137]:
# Step 1: Collect all unique pseudonyms
all_pseudonyms = set()

# Add from solo
all_pseudonyms.update(solo_dict_map['all_seps']['probability'].keys())

# Add from separated solo
all_pseudonyms.update(separated_solo_dict_map['first_solo']['probability'].keys())
all_pseudonyms.update(separated_solo_dict_map['second_solo']['probability'].keys())

# Add from social
all_pseudonyms.update(social_dict_map['all_seps']['probability'].keys())

# Step 2: Build the full dictionary
results = {}

for pseudonym in all_pseudonyms:
    results[pseudonym] = {
        # Experiment date
        "experiment_date": solo_dates.get(pseudonym, np.nan),

        # Combined solo
        "pH_H_first_vis_combined_solo_sep1": solo_dict_map['sep_1']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_combined_solo_sep2": solo_dict_map['sep_2']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_combined_solo_sep4": solo_dict_map['sep_4']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_combined_solo_all_seps": solo_dict_map['all_seps']['probability'].get(pseudonym, np.nan),

        # Separate solo
        "pH_H_first_vis_first_solo_all_seps": separated_solo_dict_map['first_solo']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_second_solo_all_seps": separated_solo_dict_map['second_solo']['probability'].get(pseudonym, np.nan),

        # Social
        "pH_H_first_vis_social_sep1": social_dict_map['sep_1']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_social_sep2": social_dict_map['sep_2']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_social_sep4": social_dict_map['sep_4']['probability'].get(pseudonym, np.nan),
        "pH_H_first_vis_social_all_seps": social_dict_map['all_seps']['probability'].get(pseudonym, np.nan),
    }

# Step 3: Convert to DataFrame
df = pd.DataFrame.from_dict(results, orient='index')


In [138]:
df

experiment_date  pH_H_first_vis_combined_solo_sep1  pH_H_first_vis_combined_solo_sep2  pH_H_first_vis_combined_solo_sep4  pH_H_first_vis_combined_solo_all_seps  pH_H_first_vis_first_solo_all_seps  pH_H_first_vis_second_solo_all_seps  pH_H_first_vis_social_sep1  pH_H_first_vis_social_sep2  pH_H_first_vis_social_sep4  pH_H_first_vis_social_all_seps
SP17      2024-10-17                                NaN                                NaN                                NaN                            0.923076923                                 NaN                          1.000000000                 0.700000000                 0.700000000                 0.857142857                     0.740740741
VC20      2024-11-20                        0.909090909                        1.000000000                        1.000000000                            0.961538462                         0.900000000                          1.000000000                 0.928571429                 0.866666667                 0.812500000                     0.866666667
IN04      2025-02-04                        0.909090909                                NaN                        1.000000000                            0.947368421                         0.909090909                          1.000000000                 1.000000000                         NaN                         NaN                     1.000000000
JL19      2025-03-19                        1.000000000                                NaN                        1.000000000                            1.000000000                         1.000000000                                  NaN                 0.916666667                 0.714285714                 0.200000000                     0.620689655
BC03      2024-12-03                        1.000000000                                NaN                                NaN                            1.000000000                                 NaN                          1.000000000                 1.000000000                 0.714285714                 0.933333333                     0.896551724
...              ...                                ...                                ...                                ...                                    ...                                 ...                                  ...                         ...                         ...                         ...                             ...
LS21      2025-04-21                        1.000000000                                NaN                        1.000000000                            1.000000000                         1.000000000                          1.000000000                 0.454545455                         NaN                 0.714285714                     0.454545455
NN03      2024-12-03                        1.000000000                                NaN                        0.857142857                            0.956521739                         0.928571429                          1.000000000                 0.785714286                 0.666666667                         NaN                     0.714285714
KS20      2024-12-20                                NaN                        0.846153846                                NaN                            0.800000000                         0.923076923                          0.666666667                 0.428571429                 0.250000000                         NaN                     0.275862069
HQ01      2025-04-01                        1.000000000                        1.000000000                        1.000000000                            1.000000000                         1.000000000                          1.000000000                         NaN                         NaN                         NaN                     0.615384615
AW19      2025-03-19                        1.000000000                        1.000000000                     

df for denominators (trial counts)

In [146]:
# Step 1: Collect all unique pseudonyms
all_pseudonyms = set()

# Add from solo
all_pseudonyms.update(solo_dict_map['all_seps']['denominator'].keys())

# Add from separated solo
all_pseudonyms.update(separated_solo_dict_map['first_solo']['denominator'].keys())
all_pseudonyms.update(separated_solo_dict_map['second_solo']['denominator'].keys())

# Add from social
all_pseudonyms.update(social_dict_map['all_seps']['denominator'].keys())

# Step 2: Build the full dictionary
results = {}

for pseudonym in all_pseudonyms:
    results[pseudonym] = {
        # Experiment date
        "experiment_date": solo_dates.get(pseudonym, np.nan),

        # Combined solo
        "pH_H_first_combined_solo_sep1": solo_dict_map['sep_1']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_combined_solo_sep2": solo_dict_map['sep_2']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_combined_solo_sep4": solo_dict_map['sep_4']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_combined_solo_all_seps": solo_dict_map['all_seps']['denominator'].get(pseudonym, np.nan),

        # Separate solo
        "pH_H_first_first_solo_all_seps": separated_solo_dict_map['first_solo']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_second_solo_all_seps": separated_solo_dict_map['second_solo']['denominator'].get(pseudonym, np.nan),

        # Social
        "pH_H_first_social_sep1": social_dict_map['sep_1']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_social_sep2": social_dict_map['sep_2']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_social_sep4": social_dict_map['sep_4']['denominator'].get(pseudonym, np.nan),
        "pH_H_first_social_all_seps": social_dict_map['all_seps']['denominator'].get(pseudonym, np.nan),
    }

# Step 3: Convert to DataFrame
denom_df = pd.DataFrame.from_dict(results, orient='index')


P(H|H first vis) - P(H|L first vis) --> compute after making dataframe

In [140]:
df.to_csv('individual_analyses_table.csv')

In [151]:
denom_df.to_csv('individual_analyses_trial_counts.csv')

In [150]:
denom_df

experiment_date  pH_H_first_combined_solo_sep1  pH_H_first_combined_solo_sep2  pH_H_first_combined_solo_sep4  pH_H_first_combined_solo_all_seps  pH_H_first_first_solo_all_seps  pH_H_first_second_solo_all_seps  pH_H_first_social_sep1  pH_H_first_social_sep2  pH_H_first_social_sep4  pH_H_first_social_all_seps
SP17      2024-10-17                            4.0                            6.0                            3.0                               13.0                             6.0                              7.0                      10                      10                       7                          27
VC20      2024-11-20                           11.0                            7.0                            8.0                               26.0                            10.0                             16.0                      14                      15                      16                          45
IN04      2025-02-04                           11.0                            1.0                            7.0                               19.0                            11.0                              8.0                       8                       5                       4                          17
JL19      2025-03-19                            7.0                            5.0                            7.0                               19.0                            15.0                              4.0                      12                       7                      10                          29
BC03      2024-12-03                           11.0                            6.0                            1.0                               18.0                             6.0                             12.0                       7                       7                      15                          29
...              ...                            ...                            ...                            ...                                ...                             ...                              ...                     ...                     ...                     ...                         ...
LS21      2025-04-21                            9.0                            5.0                           10.0                               24.0                            13.0                             11.0                      11                       4                       7                          22
NN03      2024-12-03                           12.0                            4.0                            7.0                               23.0                            14.0                              9.0                      14                       9                       5                          28
KS20      2024-12-20                            6.0                           13.0                            6.0                               25.0                            13.0                             12.0                       7                      16                       6                          29
HQ01      2025-04-01                           11.0                            9.0                            7.0                               27.0                            13.0                             14.0                       6                       4                       3                          13
AW19      2025-03-19                           24.0                            9.0                           10.0                               43.0                            18.0                             25.0                      18                      11                       8                          37

[100 rows x 11 columns]